In [ ]:
!pip install pandas
!pip install pyproj

In [1]:
import pandas as pd
import json
from datetime import datetime
import pyproj
import json

In [2]:
# convert a pandas dataframe to geojson

def df_to_geojson(df, properties, lat='latitude', lon='longitude'):
    geojson = {'type':'FeatureCollection', 'features':[]}
    
    for _, row in df.iterrows():
        feature = {'type':'Feature',
                   'properties':{},
                   'geometry':{'type':'Point',
                               'coordinates':[]}}
        
        feature['geometry']['coordinates'] = [row[lon], row[lat]]
        for prop in properties:
            feature['properties'][prop] = row[prop]
        geojson['features'].append(feature)
    
    return geojson

In [3]:
# get GeoJSON trajectories from Track.h5 file, which is the trajectory output from Tobac algorithm

starttime =  pd.to_datetime("2022-05-04 00:00:00")
endtime = pd.to_datetime("2022-05-04 23:55:00")

trajectories = pd.read_hdf('./Track.h5', key='table') # Track.h5, output from Tobac algorithm
trajectories = trajectories[(trajectories['time'] >= starttime) & (trajectories['time'] <= endtime)] # only get times between start end end

properties = ['cell', 'threshold_value', 'timestr']
geojson_trajectories = df_to_geojson(trajectories, properties, lat='y', lon='x')

json.dumps(geojson_trajectories, indent=2)

'{\n  "type": "FeatureCollection",\n  "features": [\n    {\n      "type": "Feature",\n      "properties": {\n        "cell": 1,\n        "threshold_value": 15,\n        "timestr": "2022-05-04 00:00:00"\n      },\n      "geometry": {\n        "type": "Point",\n        "coordinates": [\n          2756538.711242493,\n          1285306.6072970182\n        ]\n      }\n    },\n    {\n      "type": "Feature",\n      "properties": {\n        "cell": 2,\n        "threshold_value": 15,\n        "timestr": "2022-05-04 00:00:00"\n      },\n      "geometry": {\n        "type": "Point",\n        "coordinates": [\n          2857024.2656,\n          1261502.9755839212\n        ]\n      }\n    },\n    {\n      "type": "Feature",\n      "properties": {\n        "cell": 3,\n        "threshold_value": 15,\n        "timestr": "2022-05-04 00:00:00"\n      },\n      "geometry": {\n        "type": "Point",\n        "coordinates": [\n          2823801.3746765447,\n          1237465.0004234556\n        ]\n     

In [4]:
# save the GeoJSON file

with open('output.geojson', 'w') as output_file:
    json.dump(geojson_trajectories, output_file, indent=2)


In [6]:
# get the storm/cloud cells for a specific time string

def get_cells_by_timestr(geojson, timestr):
    cells = set()
    for feature in geojson['features']:
        if feature['properties']['timestr'] == timestr:
            cells.add(feature['properties']['cell'])
    return list(cells)

In [7]:
# get all storm/cloud cells

def get_all_cells(geojson):
    cells = set()
    for feature in geojson['features']:
        cells.add(feature['properties']['cell'])
    return list(cells)

In [ ]:
# return all time strings

def get_all_timestr(geojson):
    timestrings = set()
    for feature in geojson['features']:
        timestrings.add(feature['properties']['timestr'])
    timestrings_list = list(timestrings)
    sorted_timestrings = sorted(timestrings_list, key=lambda x: datetime.strptime(x, "%Y-%m-%d %H:%M:%S"))

    return sorted_timestrings

In [9]:
# sort features by date

def sort_features_by_date(features):
    return sorted(features, key=lambda x: x['properties']['timestr'])

In [10]:
# conveft LV95+ coordinates to WGS84 CRS

def lv95_to_web_mercator(coordinates):
    lv95 = pyproj.CRS("EPSG:2056")  # LV95 coordinate system
    web_mercator = pyproj.CRS("EPSG:4326")  # Web Mercator


    transformer = pyproj.Transformer.from_crs("EPSG:2056", "EPSG:4326")

    # Perform the coordinate transformation
    web_mercator_x, web_mercator_y = transformer.transform(coordinates[0], coordinates[1])
    return web_mercator_y, web_mercator_x

In [11]:
# get features by cell id

def get_features_by_cell_id(geojson, cell_id):
    features = []
    for feature in geojson['features']:
        if feature['properties']['cell'] == cell_id:
            features.append(feature)
    return sort_features_by_date(features)

# get features by cell id and time string 

def get_features_by_cell_id_and_timestr(geojson, cell_id, timestr):
    current_time = datetime.strptime(timestr, "%Y-%m-%d %H:%M:%S")
    features = []
    for feature in geojson['features']:
        feature_time = datetime.strptime(feature['properties']['timestr'], "%Y-%m-%d %H:%M:%S")
        if feature['properties']['cell'] == cell_id and feature_time <= current_time:
            features.append(feature)
    return sort_features_by_date(features)


In [12]:
# convert point features to polyline feature

def convert_point_features_to_polyline_feature(features):
    coordinates = []
    for feature in features:
        tmp_coordinates = lv95_to_web_mercator(feature['geometry']['coordinates'])
        coordinates.extend([tmp_coordinates])

    # Create a new GeoJSON feature with the LineString geometry
    line_feature = {
        "type": "Feature",
        "properties": {
            "cell": features[0]['properties']['cell'],  # Use dictionary notation
            "threshold_value": features[0]['properties']['threshold_value'],  # Use dictionary notation
        },
        "geometry": {
            "type": "LineString",
            "coordinates": coordinates
        }
    }
    return line_feature


In [18]:
# get trajectories by time string

def get_trajectories_by_timestr(geojson, timestr):
    line_features = []

    for cell_id in get_cells_by_timestr(geojson, timestr):
        if cell_id == 0 or cell_id == -1:
            continue
        features = get_features_by_cell_id_and_timestr(geojson, cell_id, timestr)
        line_feature = convert_point_features_to_polyline_feature(features)
        line_features.append(line_feature)


    line_geojson = {
        "type": "FeatureCollection",
        "features": line_features
    }

    return line_geojson

In [30]:
timestrings = get_all_timestr(geojson_trajectories)

['2022-05-04 00:00:00', '2022-05-04 00:05:00', '2022-05-04 00:10:00', '2022-05-04 00:15:00', '2022-05-04 00:20:00', '2022-05-04 00:25:00', '2022-05-04 00:30:00', '2022-05-04 00:35:00', '2022-05-04 00:40:00', '2022-05-04 00:45:00', '2022-05-04 00:50:00', '2022-05-04 00:55:00', '2022-05-04 01:00:00', '2022-05-04 01:05:00', '2022-05-04 01:10:00', '2022-05-04 01:15:00', '2022-05-04 01:20:00', '2022-05-04 01:25:00', '2022-05-04 01:30:00', '2022-05-04 01:35:00', '2022-05-04 01:40:00', '2022-05-04 01:45:00', '2022-05-04 01:50:00', '2022-05-04 01:55:00', '2022-05-04 02:00:00', '2022-05-04 02:05:00', '2022-05-04 02:10:00', '2022-05-04 02:15:00', '2022-05-04 02:20:00', '2022-05-04 02:25:00', '2022-05-04 02:30:00', '2022-05-04 02:35:00', '2022-05-04 02:40:00', '2022-05-04 02:45:00', '2022-05-04 02:50:00', '2022-05-04 02:55:00', '2022-05-04 03:00:00', '2022-05-04 03:05:00', '2022-05-04 03:10:00', '2022-05-04 03:15:00', '2022-05-04 03:20:00', '2022-05-04 03:25:00', '2022-05-04 03:30:00', '2022-05-0

In [ ]:
# get all trajectories and save them to a json file

results = {}

counter = 0

for timestr in get_all_timestr(geojson_trajectories):
    print(counter, timestr)
    results[timestr] = get_trajectories_by_timestr(geojson_trajectories, timestr)
    counter += 1

with open("results.json", "w") as json_file:
    json.dump(results, json_file)

0 2022-05-04 00:00:00
1 2022-05-04 00:05:00
2 2022-05-04 00:10:00
3 2022-05-04 00:15:00
4 2022-05-04 00:20:00
5 2022-05-04 00:25:00
6 2022-05-04 00:30:00
7 2022-05-04 00:35:00
8 2022-05-04 00:40:00
9 2022-05-04 00:45:00
10 2022-05-04 00:50:00
11 2022-05-04 00:55:00
12 2022-05-04 01:00:00
13 2022-05-04 01:05:00
14 2022-05-04 01:10:00
15 2022-05-04 01:15:00
16 2022-05-04 01:20:00
17 2022-05-04 01:25:00
18 2022-05-04 01:30:00
19 2022-05-04 01:35:00
20 2022-05-04 01:40:00
21 2022-05-04 01:45:00
22 2022-05-04 01:50:00
23 2022-05-04 01:55:00
24 2022-05-04 02:00:00
25 2022-05-04 02:05:00
26 2022-05-04 02:10:00
27 2022-05-04 02:15:00
28 2022-05-04 02:20:00
29 2022-05-04 02:25:00
30 2022-05-04 02:30:00
31 2022-05-04 02:35:00
32 2022-05-04 02:40:00
33 2022-05-04 02:45:00
34 2022-05-04 02:50:00
35 2022-05-04 02:55:00
36 2022-05-04 03:00:00
37 2022-05-04 03:05:00
38 2022-05-04 03:10:00
39 2022-05-04 03:15:00
40 2022-05-04 03:20:00
41 2022-05-04 03:25:00
42 2022-05-04 03:30:00
43 2022-05-04 03:35:0